In [1]:
import os
import matplotlib.pyplot as plt
import seaborn as sns
import logging as log
import pandas as pd
import seaborn as sns
import plotly.express as px
import plotly.graph_objects as go
import plotly.io as pio
from plotly.subplots import make_subplots
import geopandas as gpd
import folium

import linkingtool.linking_utility as utils
import linkingtool.linking_vis as vis

In [14]:
def create_sites_ts_plots_all_sites_2(
    resource_type: str,
    CF_ts_df: pd.DataFrame,
    save_to_dir: str):
    
    # Resample data for different time intervals
    hourly_df = CF_ts_df
    daily_df = CF_ts_df.resample('D').mean()
    weekly_df = CF_ts_df.resample('W').mean()
    monthly_df = CF_ts_df.resample('ME').mean()
    quarterly_df = CF_ts_df.resample('QE').mean()

    # Create the plot using plotly express for the hourly data
    fig = px.line(hourly_df, x=hourly_df.index, y=hourly_df.columns[0:], title=f'Hourly timeseries for {resource_type} sites',
                  labels={'value': 'CF', 'datetime': 'DateTime'}, template='ggplot2')

    # Add traces for other time intervals (daily, weekly, etc.) with dotted lines
    fig.add_trace(go.Scatter(x=daily_df.index, y=daily_df[daily_df.columns[0]], mode='lines', name='Daily', visible='legendonly',
                             line=dict(dash='dot')))
    fig.add_trace(go.Scatter(x=weekly_df.index, y=weekly_df[weekly_df.columns[0]], mode='lines', name='Weekly', visible='legendonly',
                             line=dict(dash='dot')))
    fig.add_trace(go.Scatter(x=monthly_df.index, y=monthly_df[monthly_df.columns[0]], mode='lines', name='Monthly', visible='legendonly',
                             line=dict(dash='dot')))
    fig.add_trace(go.Scatter(x=quarterly_df.index, y=quarterly_df[quarterly_df.columns[0]], mode='lines', name='Quarterly', visible='legendonly',
                             line=dict(dash='dot')))

    # Update the layout to move the legend to the right, make it scrollable, and shrink the font size
    fig.update_layout(
        legend=dict(
            orientation="v",   # Vertical legend
            yanchor="top",      # Aligns the legend at the top
            y=1,                # Moves the legend up (inside the plot area)
            xanchor="left",     # Aligns the legend on the right
            x=1.02,             # Slightly outside the plot area
            font=dict(size=10),  # Make the font size smaller
            itemwidth=30        # Reduce the width of legend items
        ),
        xaxis_title='DateTime',
        yaxis_title='CF',
        hovermode='x unified',  # Unified hover info across traces
        autosize=False,  # Allow custom sizing
        width=800,       # Adjust plot width
        height=500,      # Adjust plot height
    )

    # Add scrollable legend using CSS styling
    fig.update_layout(
        legend_title=dict(text=f'{resource_type} sites'),
        legend=dict(
            title=dict(font=dict(size=12)),  # Title size
            traceorder='normal',
            itemclick='toggleothers',
            itemdoubleclick='toggle',
            bordercolor="grey",
            borderwidth=1,
        ),
    )

    fig.update_traces(hoverinfo='name+x+y')  # Improve hover info

    # Add range selector and range slider
    fig.update_layout(
        xaxis=dict(
            rangeselector=dict(
                buttons=[
                    dict(count=1, label="1d", step="day", stepmode="backward"),
                    dict(count=7, label="1w", step="day", stepmode="backward"),
                    dict(count=1, label="1m", step="month", stepmode="backward"),
                    dict(count=3, label="3m", step="month", stepmode="backward"),
                    dict(step="all")
                ]
            ),
            rangeslider=dict(visible=True),  # Add a range slider
            type="date"
        )
    )

    # Save the plot to an HTML file
    # fig.write_html(f'{save_to_dir}/Timeseries_top_sites_{resource_type}.html')

    # Optionally display the plot
    fig.show()


In [15]:

solar_buckets_CFts_file=f"results/linking/Wind_Top_Sites_Clustered_CF_timeseries.pkl"

gdf=pd.read_pickle(solar_buckets_CFts_file)
create_sites_ts_plots_all_sites_2('wind',gdf,'results')

* To Print the Plot Generation Date

In [19]:
import datetime

# Get today's date and time
now = datetime.datetime.now()
date_time_str = now.strftime("%Y-%m-%d %H:%M:%S")

* Load Config

In [20]:
config_file_path ='config/config_linking_tool.yml'
config=utils.load_config(config_file_path)

current_region=config['regional_info']['region_1']
_CRC_=current_region['code'] #Current Region Code

# Explanation of the Config files

 * Load GADM regional data file.

In [21]:
gadm_regions_gdf = gpd.read_file(f'data/GADM/{_CRC_}/{_CRC_}_gadm_regions.geojson')

2024-09-28 12:24:35 - INFO - GDAL signalled an error: err_no=4, msg='data/GADM/BC/BC_gadm_regions.geojson: No such file or directory'


DriverError: Failed to open dataset (flags=68): data/GADM/BC/BC_gadm_regions.geojson

* Load Aeroway Data

In [37]:
aeroway=gpd.read_file(f'data/OSM/aeroway/{_CRC_}/aeroway_OSM_{_CRC_}.geojson')

 * Load Conversation lands

In [38]:
conservation_protected_lands=gpd.GeoDataFrame(pd.read_pickle(f'data/Gov/Conservation_Lands/{_CRC_}/CPCAD_{_CRC_}.pkl'))
# BC_protectedLands.explore('IUCN_CAT_desc',legend=True)

>old database

In [39]:
# conservation_lands = gpd.read_file('data/BC_gov/Conservation Lands/WCL_CONSERVATION_LANDS_SP.gdb') # old database
# Source: https://www.env.gov.bc.ca/soe/indicators/land/protected-lands-and-waters.html
# conservation_lands.explore('TENURE_TYPE',legend=True)

 * Load Transmission Lines & Substations

In [5]:
buses_gdf = gpd.GeoDataFrame(pd.read_pickle(f"data/Processed_data/Transmission/{_CRC_}/Transmission.pkl"))
print(f">> {len(buses_gdf)} Transmission Nodes Loaded")

# transmission_lines=gpd.read_file('data/BC_gov/TransmissionLine/BCGW_7113060B_1710035634909_9496/GBA_TRANSMISSION_LINES_SP.gdb')
# tx_line_length=transmission_lines['FEATURE_LENGTH_M'].sum()/1E6
# print(f">> {tx_line_length:.2f} Th.km Transmission Lines Loaded")

>> 939 Transmission Nodes Loaded


 * Load Existing Sites

In [6]:
existing_resources='data/BC_gov/PowerPlantsRenewGE1MW_NorthAmerica_201708_SHP'
existing_resources=gpd.read_file(existing_resources)

BC_mask = (existing_resources['Country'] == 'Canada') & (existing_resources['StateProv'] == 'British Columbia')

BC_existing_VRE=existing_resources[BC_mask]

wind_mask=BC_existing_VRE['Wind_MW']>0
solar_mask=BC_existing_VRE['Solar_MW']>0

Wind_existing=BC_existing_VRE[wind_mask]
Solar_existing=BC_existing_VRE[solar_mask]

Wind_existing=Wind_existing.loc[:,['Country', 'Facility', 'Owner', 'Operator', 'Latitude', 'Longitude',
       'City', 'County', 'StateProv', 'ZipCode', 'Address',
       'Wind_MW', 'Source', 'Period','geometry']]

Solar_existing=Solar_existing.loc[:,['Country', 'Facility', 'Owner', 'Operator', 'Latitude', 'Longitude',
       'City', 'County', 'StateProv', 'ZipCode', 'Address',
       'Solar_MW', 'Source', 'Period','geometry']]

generators_existing=pd.read_csv('/local-scratch/localhome/mei3/eliasinul/repositories/PyPSA_BC/data/SESIT/CODERS/data-pull/supply/generators.csv')
BC_mask=generators_existing.operating_region=='British Columbia'
gen_existing_BC=generators_existing[BC_mask]

# CODERS data
wind_gen_existing_BC_wind=gen_existing_BC[gen_existing_BC.gen_type_copper=='wind']

df=wind_gen_existing_BC_wind
# Assuming your DataFrame is named 'df' and has columns 'latitude' and 'longitude'
geometry = [Point(xy) for xy in zip(df['longitude'], df['latitude'])]
crs = {'init': 'epsg:4326'}  # Assuming WGS 84 coordinate reference system
wind_gen_existing_BC_wind_gdf = gpd.GeoDataFrame(df, geometry=geometry, crs=crs)


DriverError: Failed to open dataset (flags=68): data/BC_gov/PowerPlantsRenewGE1MW_NorthAmerica_201708_SHP

## From Linking Tool

 * Load Solar Sites 

NameError: name 'pd' is not defined

/local-scratch/localhome/mei3/eliasinul/repositories/Linking_tool/linkingtool/linking_vis.py:284: FutureWarning:

'M' is deprecated and will be removed in a future version, please use 'ME' instead.

/local-scratch/localhome/mei3/eliasinul/repositories/Linking_tool/linkingtool/linking_vis.py:285: FutureWarning:

'Q' is deprecated and will be removed in a future version, please use 'QE' instead.



In [8]:
solar_buckets_file=f"results/Solar_Top_Sites_Clustered.pkl"
solar_buckets_CFts_file=f"results/linking/Solar_Top_Sites_Clustered_CF_timeseries.pkl"

# Convert DataFrames to GeoDataFrames for buses
solar_buckets_gdf = pd.read_pickle(solar_buckets_file)
solar_buckets_CFts = pd.read_pickle(solar_buckets_CFts_file)

solar_buckets_gdf_all = pd.read_pickle(f'data/Processed_data/Solar/{_CRC_}/cell_cluster_gdf_filtered_finalSites_{_CRC_}.pkl')

FileNotFoundError: [Errno 2] No such file or directory: 'results/Solar_Top_Sites_Clustered.pkl'

In [13]:
Solar_existing

Country   Facility              Owner Operator   Latitude   Longitude  \
5734  Canada  Kimberley  City of Kimberley  Sunmine  49.669012 -115.947628   

           City County         StateProv ZipCode Address  Solar_MW  \
5734  Kimberley   None  British Columbia    None    None       1.0   

                   Source  Period                     geometry  
5734  BC Hydro IPP supply  201704  POINT (-115.94763 49.66901)

In [17]:
import folium
m=gadm_regions_gdf.explore(style_kwds={'fillOpacity': 0.1}, name=f'Admin Regions - {current_region['code']} ')
solar_buckets_gdf.explore("Region",m=m,style_kwds={'fillOpacity': 0.7}, name=f'Potential Solar Sites - {current_region['code']} ')
Solar_existing.explore(m=m,style_kwds={'fillOpacity': 0.7}, name=f'Existing Solar Sites - {current_region['code']}')

# Add layer control
folium.LayerControl().add_to(m)

# Display the map
m.save(f'vis/Solar/{current_region['code']}_Solar_Resource_Options_map.html')
m

 * Load Wind Data

In [43]:
wind_buckets_gdf_all = pd.read_pickle('data/Processed_data/Wind/cell_cluster_gdf_filtered_finalSites.pkl')
wind_buckets_file="results/Wind_Top_Sites_Clustered.pkl"
wind_buckets_CFts_file="results/Wind_Top_Sites_Clustered_CF_timeseries.pkl"

# Convert DataFrames to GeoDataFrames for buses
wind_buckets_gdf = pd.read_pickle(wind_buckets_file)
wind_buckets_CFts = pd.read_pickle(wind_buckets_CFts_file)

FileNotFoundError: [Errno 2] No such file or directory: 'data/Processed_data/Wind/cell_cluster_gdf_filtered_finalSites.pkl'

In [ ]:
# wind_buckets_CFts['Fraser-Fort George_1']['2022-01-01'].plot()

* How many Turbines We need to Place ?

In [ ]:
wind_turbine_nominal_capacity:int=config['wind']['turbines']['OEDB']['model_2_P'] #MW
wind_buckets_gdf['No_of_turbines'] = np.floor(wind_buckets_gdf['potential_capacity'] / wind_turbine_nominal_capacity).astype(int)
mask=wind_buckets_gdf.potential_capacity>=wind_turbine_nominal_capacity
len(wind_buckets_gdf[mask])
# wind_buckets_gdf[mas].head(10).explore('potential_capacity')

In [ ]:
solar_buckets_gdf.to_file('results/ESRI_shapefiles/solar.shp', driver="ESRI Shapefile")


In [ ]:
# Export DataFrame to Excel
wind_buckets_gdf.to_excel('results/wind_buckets.xlsx', index=False)  # 'index=False' prevents writing row numbers
solar_buckets_gdf.to_excel('results/solar_buckets.xlsx', index=False)  # 'index=False' prevents writing row numbers

## For Plotting in PowerBI

In [ ]:
def create_WKT_file(gdf,file_name):

    # Convert geometries to WKT format
    gdf['WKT'] = gdf['geometry'].apply(lambda x: x.wkt)

    # Convert to a DataFrame and drop the geometry column
    solar_buckets_df_powerBI = pd.DataFrame(gdf.drop(columns='geometry'))
    # Create the directory if it doesn't exist
    save_to='results/forPowerBI'
    if not os.path.exists(save_to):
        os.makedirs(save_to)
    # Save to CSV
    gdf.to_csv(os.path.join(save_to,file_name), index=False)

    return print(f'WKT file Created and saved to {save_to}')

In [ ]:
create_WKT_file(solar_buckets_gdf,'Solar_Clusters_WKT.csv')
create_WKT_file(wind_buckets_gdf,'Wind_Clusters_WKT.csv')

In [ ]:
solar_buckets_gdf_powerBI=solar_buckets_gdf.copy()

# Convert geometries to WKT format
solar_buckets_gdf_powerBI['WKT'] = solar_buckets_gdf_powerBI['geometry'].apply(lambda x: x.wkt)

# Convert to a DataFrame and drop the geometry column
solar_buckets_df_powerBI = pd.DataFrame(solar_buckets_gdf_powerBI.drop(columns='geometry'))

# Save to CSV
solar_buckets_gdf_powerBI.to_csv('results/SOLAR_geodata_wkt.csv', index=False)


# Visualization

## Static

In [ ]:
import matplotlib.pyplot as plt
import matplotlib.patches as mpatches
import cartopy.crs as ccrs
import cartopy.feature as cfeature

In [ ]:
# Create the figure and axes
fig = plt.figure(figsize=(12, 7))
ax = plt.axes(projection=ccrs.PlateCarree())

# Set the title
plt.title("Potential Solar and Wind Sites - BC")

# Potential Solar Sites
solar_buckets_gdf=  solar_buckets_gdf #solar_buckets_gdf_all
solar_buckets_gdf.plot('CF_mean', ax=ax, alpha=0.6, color="Green")

# Add the green text "Potential Solar Sites" on the right side of the plot
plt.text(0.95, 0.41, f"Potential\nSolar Sites\n[CF ~ {round(solar_buckets_gdf.CF_mean.mean(),3)}]",
         transform=ax.transAxes, fontsize=10, color='green', ha='right', va='center')

# Potential Wind Sites
wind_buckets_gdf= wind_buckets_gdf #wind_buckets_gdf_all
wind_buckets_gdf_plot = wind_buckets_gdf.plot('CF_mean', ax=ax, cmap='RdPu')
cmap_wind = plt.cm.ScalarMappable(cmap='RdPu')
cmap_wind.set_array(wind_buckets_gdf['CF_mean'])
cbar_wind = plt.colorbar(cmap_wind, ax=ax, orientation='vertical', fraction=0.02, pad=0.08,
                         label="Potential Wind sites' CF")

# Existing Wind Sites
wind_gen_existing_BC_wind_gdf.plot('capacity_factor_in_%', ax=ax, markersize='install_capacity_in_mw', alpha=0.4,
                                   cmap='YlOrRd')
cmap_wind_ex = plt.cm.ScalarMappable(cmap='YlOrRd')
cmap_wind_ex.set_array(wind_gen_existing_BC_wind_gdf['capacity_factor_in_%'])
cbar_wind_ex = plt.colorbar(cmap_wind_ex, ax=ax, orientation='vertical', fraction=0.02, pad=0.02,
                            label="Existing Wind sites' CF")

# GADM Boundaries
gadm_regions_gdf.plot(ax=ax, alpha=0.5, edgecolor='grey', color="None")

# Baseline map features
ax.add_feature(cfeature.COASTLINE, linewidth=0.5)
ax.add_feature(cfeature.BORDERS, linewidth=0.5)
ax.add_feature(cfeature.OCEAN, color="azure")
ax.add_feature(cfeature.RIVERS, alpha=0.6)
ax.add_feature(cfeature.LAKES, alpha=0.7)
ax.add_feature(cfeature.LAND, color="cornsilk", alpha=0.5)

# Conservation & Protected lands
BC_protectedLands.plot(ax=ax, alpha=0.4, color='slategrey')
category1 = "Canadian Protected and\nConserved Areas Database\n(CPCAD-2023)"
legend_handles1 = [mpatches.Patch(color='slategrey', label=category1)]

# # BC Ferries terminals
# BCFerries_operator.plot(ax=ax, alpha=0.7, color='turquoise')
# category2 = "BC-Ferries Terminal"
# legend_handles2 = [mpatches.Patch(color='turquoise', label=category2)]

# Merge legend handles and labels
legend_handles = legend_handles1 #+ legend_handles2
legend_labels = [handle.get_label() for handle in legend_handles]

# Plot combined legend
plt.legend(legend_handles, legend_labels, loc='upper right', fontsize=7)

# Include the Texts in Plot
plt.text(0.03, 0.05, f"WIND\n"
                     f"Existing : {wind_gen_existing_BC_wind_gdf.install_capacity_in_mw.sum()*1E-3} GW\n"
                     f"Potential : {round(wind_buckets_gdf.potential_capacity.sum()*1E-3,1)} GW\n\n"
                     f"SOLAR\n"
                     f"Existing : {Solar_existing.Solar_MW.sum()*1E-3} GW\n"
                     f"Potential : {round(solar_buckets_gdf.potential_capacity.sum()*1E-3,1)} GW",
         transform=ax.transAxes, fontsize=10, bbox=dict(facecolor='gray', alpha=0.5, edgecolor='none'))

# Include the Texts in Plot
plt.text(0.009, -0.04,
         f"The potential assessment for Solar and Wind capacity expansion has been capped to the values as mentioned. "
         f"Powered by ERA5 Reanalysis Weather Data (2022).\nExisting resources as of March 2024. "
         f"Status of the work: In progress. Plot Generated on: {date_time_str}",
         transform=ax.transAxes, fontsize=7, bbox=dict(facecolor='gray', alpha=0.2, edgecolor='none'))

plt.tight_layout()

# Save the Figure Locally
plt.savefig('vis/ExistingVSTool_sites.png', dpi=600, bbox_inches='tight')
plt.savefig('results/ExistingVSTool_sites.png', dpi=600, bbox_inches='tight')

plt.show()


## Interactive Map

* Road Network

In [ ]:
# roads=gpd.read_file('data/BC_gov/RoadNetwork/NRN_BC_14_0_SHAPE_en/NRN_BC_14_0_ROADSEG.shp')
# roads=roads.to_crs(gadm_regions_gdf.crs)
# print(f">>Road Segments Loaded")

In [ ]:
# transmission_lines=transmission_lines.loc[:, ['TRANSMISSION_LINE_ID', 'FEATURE_LENGTH_M', 'geometry']]
# transmission_lines.to_crs(gadm_regions_gdf.crs)

* Road Network

In [ ]:
# from folium.plugins import MarkerCluster
# # Initialize the map
# m = fl.Map(zoom_start=5, tiles="OpenStreetMap")

# # Add boundary to the map with a popup
# boundary_group = fl.FeatureGroup(name='BC Area').add_to(m)

# for _, r in gadm_regions_gdf.iterrows():
#     sim_geo = gpd.GeoSeries(r["geometry"]).simplify(tolerance=0.001)
#     geo_j = sim_geo.to_json()
#     geo_j = fl.GeoJson(data=geo_j, style_function=lambda x: {
#         "fillColor": "yellow",
#         "color": "navy",
#         "weight": 0.3
#     })
#     fl.Popup("BC Area").add_to(geo_j)
#     geo_j.add_to(boundary_group)

# # Protected and Conservation Lands
# protected_conservation_lands = BC_protectedLands.to_json()
# fl.GeoJson(
#     protected_conservation_lands,
#     name='Conservation & Protected Area',
#     tooltip=fl.GeoJsonTooltip(fields=['IUCN_CAT_desc'], aliases=['IUCN Category'], labels=True),
#     style_function=lambda feature: {
#         'fillOpacity': 0.5,  # Adjust opacity as needed (0 is fully transparent, 1 is fully opaque)
#         'fillColor': 'red',  # Specify the color of the polygons
#         'color': 'black',  # Specify the color of the borders
#         'weight': 0.3  # Specify the weight of the borders
#     },
#     overlay=True
# ).add_to(m)

# # # Aeroway
# # bc_aeroway = bc_aeroway_buffered.to_json()
# # fl.GeoJson(
# #     bc_aeroway,
# #     name='Aeroway',
# #     tooltip=fl.GeoJsonTooltip(fields=['aeroway'], aliases=['Type of Aeroway'], labels=True),
# #     style_function=lambda feature: {
# #         'fillOpacity': 0.5,  # Adjust opacity as needed (0 is fully transparent, 1 is fully opaque)
# #         'fillColor': 'plum',  # Specify the color of the polygons
# #         'color': 'black',  # Specify the color of the borders
# #         'weight': 0.3  # Specify the weight of the borders
# #     },
# #     overlay=True
# # ).add_to(m)

# # Roads
# # bc_roads = roads.to_json()
# # fl.GeoJson(
# #     bc_roads,
# #     name='Provincial Road Network',
# #     tooltip=fl.GeoJsonTooltip(fields=['R_STNAME_C'], aliases=['Road_name:'], labels=True),
# #     style_function=lambda feature: {
# #         'fillOpacity': 0.5,  # Adjust opacity as needed (0 is fully transparent, 1 is fully opaque)
# #         'fillColor': 'slategray',  # Specify the color of the polygons
# #         'color': 'gray',  # Specify the color of the borders
# #         'weight': 0.5  # Specify the weight of the borders
# #     },
# #     overlay=True
# # ).add_to(m)

# # TX lines
# # bc_tx_lines = transmission_lines.to_json()
# # fl.GeoJson(
# #     bc_tx_lines,
# #     name='Provincial Grid Lines',
# #     tooltip=fl.GeoJsonTooltip(fields=['TRANSMISSION_LINE_ID'], aliases=['Line_ID'], labels=True),
# #     style_function=lambda feature: {
# #         'fillOpacity': 0.5,  # Adjust opacity as needed (0 is fully transparent, 1 is fully opaque)
# #         'fillColor': 'lightcoral',  # Specify the color of the polygons
# #         'color': 'indianred',  # Specify the color of the borders
# #         'weight': 0.5  # Specify the weight of the borders
# #     },
# #     overlay=True
# # ).add_to(m)


# # Create separate MarkerCluster layer group for nodes
# marker_cluster_nodes = MarkerCluster(name='Grid Nodes (black)').add_to(m)
# # Add wind sites to the MarkerCluster
# for _, r in buses_gdf.iterrows():
#     location = [r['geometry'].y, r['geometry'].x]
#     popup_text1 = f"Node: {r['name']}"
#     fl.Marker(location=location, popup=fl.Popup(popup_text1), icon=fl.Icon(color='black')).add_to(marker_cluster_nodes)

# # Add a choropleth layer for Sites with the name 'Capacity Heat Map'
# choropleth_wind = fl.Choropleth(
#     geo_data=wind_buckets_gdf,
#     data=wind_buckets_gdf['potential_capacity'],
#     fill_color="Blues",
#     fill_opacity=0.6,
#     line_opacity=0.2,
#     key_on="feature.id",
#     name=f'Wind Capacity (MW) [Blues]'  # Set the name here
# ).add_to(m)

# # Add a choropleth layer for Sites with the name 'Capacity Heat Map'
# choropleth_solar = fl.Choropleth(
#     geo_data=solar_buckets_gdf,
#     data=solar_buckets_gdf['potential_capacity'],
#     fill_color="Purples",
#     fill_opacity=0.6,
#     line_opacity=0.2,
#     key_on="feature.id",
#     name=f'Solar Capacity (MW) [Purples]'  # Set the name here
# ).add_to(m)

# # Create a MarkerCluster for Wind_existing
# marker_cluster_wind_existing = MarkerCluster(name='Wind Existing Sites (Blue)').add_to(m)

# # Add wind sites to the MarkerCluster
# for _, r in Wind_existing.iterrows():
#     location = [r['geometry'].y, r['geometry'].x]
#     popup_text1 = f"Wind: {int(r['Wind_MW'])} MW"
#     popup_text2 = f"Owner: {r['Owner']}" 
#     popup_text3 = f"Operator: {r['Operator']}"
#     popup_text4 = f"Estd.: {r['Period']}"
#     combined_popup_text = f"{popup_text1}<br>{popup_text2}<br>{popup_text3}<br>{popup_text4}"
    
#     fl.Marker(location=location, popup=fl.Popup(combined_popup_text), icon=fl.Icon(color='blue')).add_to(marker_cluster_wind_existing)

# # Create a MarkerCluster for Wind_existing
# marker_cluster_solar_existing = MarkerCluster(name='Solar Existing Sites (Red)').add_to(m)

# # Add wind sites to the MarkerCluster
# for _, r in Solar_existing.iterrows():
#     location = [r['geometry'].y, r['geometry'].x]
#     popup_text1 = f"Solar: {int(r['Solar_MW'])} MW"
#     popup_text2 = f"Owner: {r['Owner']}" 
#     popup_text3 = f"Operator: {r['Operator']}"
#     popup_text4 = f"Estd.: {r['Period']}"
#     combined_popup_text = f"{popup_text1}<br>{popup_text2}<br>{popup_text3}<br>{popup_text4}"
    
#     fl.Marker(location=location, popup=fl.Popup(combined_popup_text), icon=fl.Icon(color='red')).add_to(marker_cluster_solar_existing)


# # Add a legend to the top right corner
# fl.LayerControl(position='topright', collapsed=False).add_to(m)

# # Save the map
# # map_save_path = os.path.join('results', 'VRE_Sites_map.html')
# # m.save(map_save_path)
# # m.save('index.html')
# # Display the map
# m


In [ ]:
# m.save('index.html')